In [2]:
import sys
import os

sys.path.insert(0, '../src') # add library code to path

In [1]:
from wikiparser import download_enwiki_zips

zip_outdir = "../data/raw/zips"

download_enwiki_zips(1, zip_outdir , False)

ModuleNotFoundError: No module named 'wikiparser'

In [11]:
zips = os.listdir(zip_outdir)
zips

['enwiki-20200101-0.7z']

In [12]:
from wikiparser import extract_7zip

extract_outdir = "../data/raw/extracted"

for zip_file in os.listdir(zip_outdir ):
    if zip_file[-2:] == "7z":
        extract_7zip(zip_outdir + "/" + zip_file, extract_outdir)

Extracted file already exists: ../data/raw/extracted/enwiki-20200101-0


In [14]:
class Revision:
    def __init__(self, timestamp, revert, version, contributor, revision_id, revision_parentid, sha1, text_len):
        self.timestamp = timestamp
        self.revert = revert
        self.version = version
        self.contributor = contributor
        self.revision_id = revision_id
        self.revision_parentid = revision_parentid
        self.sha1 = sha1
        self.text_len = text_len
        
    def __repr__(self):
        return [self.timestamp, self.revert, self.version, self.contributor, self.revision_id, self.revision_parentid]
        
    def __str__(self):
        try:
            return "^^^_" + self.timestamp + " " + str(self.revert) + " " + str(self.version) + " " + str(self.text_len) + " " + self.contributor
        except:
            print(self.timestamp)
            print(self.revert)
            print(self.version)
            print(self.contributor)
    
    def get_revision_id(self):
        return self.revision_id

In [19]:
#parse the file, calculate lightdump information, output to outfile
def parse_enwiki_to_lightdump(filepath, outfile, outdir, articles=[]):

    from lxml import etree
    import re

    context = etree.iterparse(filepath, tag='{http://www.mediawiki.org/xml/export-0.10/}page', encoding='utf-8')
    nsmap = {'ns': 'http://www.mediawiki.org/xml/export-0.10/'}

    article_count = len(articles) if len(articles) != 0 else -1
    
    revi_header = "^^^_"

    page_dicts = {}
            
    if not os.path.exists(outdir):
        os.makedirs(outdir, exist_ok=True)

    with open(outdir + "/" + outfile, 'w') as file:
        file.write("")

    for event, elem in context:

        page_title = '_'.join(elem.find('ns:title', nsmap).text.split())
        page_id = elem.find('ns:id', nsmap).text
        revisions = elem.findall('ns:revision', nsmap)

        rev_dicts = []
        
        if len(articles) != 0 and page_title not in articles:
            elem.clear()
            while elem.getprevious() is not None:
                del elem.getparent()[0]
            continue
        
#         print(page_title)
#         print(len(revisions))
        
        for revision in revisions:
            rev = {}
            
            rev['revision_id'] = revision.find("ns:id", nsmap).text
            rev['revision_parentid'] = revision.find("ns:parentid", nsmap).text if revision.find("ns:parentid", nsmap) != None else None
            rev['timestamp'] = revision.find("ns:timestamp", nsmap).text
            rev['sha1'] = revision.find("ns:sha1", nsmap).text
            
#             print()
#             print("PRINTING TEXT LENGTH FOR: " + page_title + " ===================================================")
            revision_text = revision.find("ns:text", nsmap).text
            if revision_text != None:
#                 revision_text = re.sub(r'<[^>]+>', " ", revision.find("ns:text", nsmap).text)
#                 revision_text = re.sub(r'((http[s]?|ftp):\/)?\/?([^:\/\s]+)((\/\w+)*\/)([\w\-\.]+[^#?\s]+)(.*)?(#[\w\-]+)?', 'URL_ADDRESS_REPLACEMENT', revision_text)
#                 revision_text = re.sub(r'[,.;#?|!&$]+', ' ', revision_text)
#                 revision_text = re.sub(r'[\{\}()\*\[\]\'\"=-]+', '', revision_text)
                rev['text_len'] = len(revision_text.split())
                
#                 if rev['text_len'] < 500:
#                     print(revision_text.split())
#                     print(rev['text_len'])
#                     print()
            else:
                rev['text_len'] = 0
                
            
             
            #getting contributer info
            contributor_info = revision.find("ns:contributor", nsmap)
            revision_contributor_username = contributor_info.find("ns:username", nsmap).text if contributor_info.find("ns:username", nsmap) != None else None
            revision_contributor_id = contributor_info.find("ns:id", nsmap).text if contributor_info.find("ns:id", nsmap) != None else None
            revision_contributor_ip = contributor_info.find("ns:ip", nsmap).text if contributor_info.find("ns:ip", nsmap) != None else None
            
            if revision_contributor_username != None:
                revision_contributor_username = "_".join(revision_contributor_username.split())
                rev['contributor'] = revision_contributor_username
            elif revision_contributor_ip != None:
                rev['contributor'] = revision_contributor_ip
            else:
                rev['contributor'] = "null"
                
            rev_dicts.append(rev)
            
        rev_dicts.sort(key=lambda x: x['timestamp'])

        version = 1
        page_results = []

        for i in range(len(rev_dicts)):

            temp_rev = Revision(rev_dicts[i]['timestamp'], 0, version, rev_dicts[i]['contributor'], \
                                rev_dicts[i]['revision_id'], rev_dicts[i]['revision_parentid'], \
                                rev_dicts[i]['sha1'], rev_dicts[i]['text_len'])
            if rev_dicts[i]['revision_parentid'] == None:
                page_results.append(temp_rev)
                version += 1    
            else:
                # find the point we revert to
                min_ind = len(page_results) - 1
                while min_ind > 0:
                    if page_results[min_ind].sha1 == rev_dicts[i]['sha1']:
                        temp_rev.version = page_results[min_ind].version
                        temp_rev.revert = 1
                        page_results.append(temp_rev)
                        break
                    min_ind -= 1

                if min_ind == 0:
                    page_results.append(temp_rev)
                    version += 1
        
        if len(articles) == 0 or page_title in articles:
            article_count -= 1
    
            print("Writing {} {} revisions to {}".format(page_title, len(page_results), outfile))
            with open(outdir + "/" + outfile, 'a') as file:
                with open(outdir + "/" + 'article_titles.txt', 'a') as article_file:
                    file.write(page_title.strip() + '\n')
                    article_file.write(page_title.strip() + "\n")
                    for i in range(len(page_results) - 1, -1, -1):
                        file.write(page_results[i].__str__() + "\n")
            
        # release uneeded XML from memory
        elem.clear()
        while elem.getprevious() is not None:
            del elem.getparent()[0]

        if article_count != -1 and article_count == 0:
            break

    del context

In [20]:

#parse enwiki to lightdump
file_to_parse = "../data/raw/extracted/enwiki-20200101-0"
lightdump_filename = "popularitydump.txt"
temp_dir = "../data/temp"
articles = []

parse_enwiki_to_lightdump(file_to_parse , lightdump_filename, temp_dir, articles)

Writing AccessibleComputing 13 revisions to popularitydump.txt
Writing Anarchism 18885 revisions to popularitydump.txt
Writing AfghanistanHistory 6 revisions to popularitydump.txt
Writing AfghanistanGeography 7 revisions to popularitydump.txt
Writing AfghanistanPeople 8 revisions to popularitydump.txt
Writing AfghanistanCommunications 5 revisions to popularitydump.txt
Writing AfghanistanTransportations 9 revisions to popularitydump.txt
Writing AfghanistanMilitary 6 revisions to popularitydump.txt
Writing AfghanistanTransnationalIssues 5 revisions to popularitydump.txt
Writing AssistiveTechnology 6 revisions to popularitydump.txt
Writing AmoeboidTaxa 8 revisions to popularitydump.txt
Writing Autism 10276 revisions to popularitydump.txt
Writing AlbaniaHistory 6 revisions to popularitydump.txt
Writing AlbaniaPeople 5 revisions to popularitydump.txt
Writing AsWeMayThink 6 revisions to popularitydump.txt
Writing AlbaniaGovernment 5 revisions to popularitydump.txt
Writing AlbaniaEconomy 6 re

Writing Asphalt 1677 revisions to popularitydump.txt
Writing American_National_Standards_Institute 575 revisions to popularitydump.txt
Writing Argument_(disambiguation) 337 revisions to popularitydump.txt
Writing Apollo_11 7166 revisions to popularitydump.txt
Writing Apollo_8 2374 revisions to popularitydump.txt
Writing Astronaut 0 revisions to popularitydump.txt
Writing A_Modest_Proposal 1225 revisions to popularitydump.txt
Writing Alkali_metal 0 revisions to popularitydump.txt
Writing Argument_form 63 revisions to popularitydump.txt
Writing Allotrope 12 revisions to popularitydump.txt
Writing Alphabet 4183 revisions to popularitydump.txt
Writing Talk:Arc_de_Triomphe 231 revisions to popularitydump.txt
Writing Atomic_number 0 revisions to popularitydump.txt
Writing Anatomy 2434 revisions to popularitydump.txt
Writing Affirming_the_consequent 339 revisions to popularitydump.txt
Writing Andrei_Tarkovsky 1381 revisions to popularitydump.txt
Writing Ambiguity 940 revisions to popularitydu

Writing Alp_Arslan 540 revisions to popularitydump.txt
Writing American_Film_Institute 593 revisions to popularitydump.txt
Writing Akira_Kurosawa 2953 revisions to popularitydump.txt
Writing Ancient_civilization 102 revisions to popularitydump.txt
Writing Ancient_Egypt 7629 revisions to popularitydump.txt
Writing Analog_Brothers 96 revisions to popularitydump.txt
Writing Motor_neuron_disease 1364 revisions to popularitydump.txt
Writing Abjad 0 revisions to popularitydump.txt
Writing Abugida 786 revisions to popularitydump.txt
Writing ABBA 8079 revisions to popularitydump.txt
Writing Allegiance 235 revisions to popularitydump.txt
Writing Absolute_majority 95 revisions to popularitydump.txt
Writing Altenberg 77 revisions to popularitydump.txt
Writing MessagePad 1039 revisions to popularitydump.txt
Writing A._E._van_Vogt 724 revisions to popularitydump.txt
Writing Anna_Kournikova 2260 revisions to popularitydump.txt
Writing Accountancy 24 revisions to popularitydump.txt
Writing Alfons_Mar

In [1]:
import sys
import os

sys.path.insert(0, '../src') # add library code to path

In [ ]:
from wikiparser import download_metadata_zips

zip_outdir = "../data/raw/zips"

download_metadata_zips(2, zip_outdir , False)

In [ ]:
zips = os.listdir(zip_outdir)
zips

In [3]:
import gzip
import shutil

def gunzip_shutil(source_filepath, dest_filepath, block_size=65536):
    with gzip.open(source_filepath, 'rb') as s_file, \
            open(dest_filepath, 'wb') as d_file:
        shutil.copyfileobj(s_file, d_file, block_size)

In [4]:
gunzip_shutil("../data/raw/zips/metadata-20200101-1.xml.gz", '../data/raw/extracted/metadata-20200101-1.xml')

In [6]:
with open("../data/raw/extracted/metadata-20200101-1.xml") as file:
    for line in file:
        print(line)

<mediawiki xmlns="http://www.mediawiki.org/xml/export-0.10/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.mediawiki.org/xml/export-0.10/ http://www.mediawiki.org/xml/export-0.10.xsd" version="0.10" xml:lang="en">

  <siteinfo>

    <sitename>Wikidata</sitename>

    <dbname>wikidatawiki</dbname>

    <base>https://www.wikidata.org/wiki/Wikidata:Main_Page</base>

    <generator>MediaWiki 1.35.0-wmf.11</generator>

    <case>first-letter</case>

    <namespaces>

      <namespace key="-2" case="first-letter">Media</namespace>

      <namespace key="-1" case="first-letter">Special</namespace>

      <namespace key="0" case="first-letter" />

      <namespace key="1" case="first-letter">Talk</namespace>

      <namespace key="2" case="first-letter">User</namespace>

      <namespace key="3" case="first-letter">User talk</namespace>

      <namespace key="4" case="first-letter">Wikidata</namespace>

      <namespace key="5" case="first-letter">Wikidat

        <username>Bene*</username>

        <id>1467</id>

      </contributor>

      <minor/>

      <model>wikitext</model>

      <format>text/x-wiki</format>

      <text bytes="3355" id="155886830" />

      <sha1>gogr0dyri4hdka5yxylpds86nx4zepl</sha1>

    </revision>

    <revision>

      <id>155487509</id>

      <parentid>155483556</parentid>

      <timestamp>2014-09-02T19:03:48Z</timestamp>

      <contributor>

        <username>Bene*</username>

        <id>1467</id>

      </contributor>

      <comment>some clean up of HTML and CSS</comment>

      <model>wikitext</model>

      <format>text/x-wiki</format>

      <text bytes="3337" id="155890816" />

      <sha1>47ic9kwdco7xgkbf9u0sk05my9rz8w4</sha1>

    </revision>

    <revision>

      <id>155496319</id>

      <parentid>155487509</parentid>

      <timestamp>2014-09-02T19:34:44Z</timestamp>

      <contributor>

        <username>Bene*</username>

        <id>1467</id>

      </contributor>

      <comment>get ri


      <text bytes="552" id="4466" />

      <sha1>9sdrjdk86b20a65isikgqaw8lx7yzt9</sha1>

    </revision>

    <revision>

      <id>4531</id>

      <parentid>4368</parentid>

      <timestamp>2012-10-30T15:32:25Z</timestamp>

      <contributor>

        <username>Stryn</username>

        <id>2936</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|fiwiki */ Afrikka</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="579" id="4629" />

      <sha1>p0cny7nirl0bvylh094fglj74i3p72l</sha1>

    </revision>

    <revision>

      <id>5876</id>

      <parentid>4531</parentid>

      <timestamp>2012-10-30T17:05:21Z</timestamp>

      <contributor>

        <username>Aplasia</username>

        <id>3540</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|itwiki */ Africa</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="605" id="5974" />

      <sha1>


    </revision>

    <revision>

      <id>44994</id>

      <parentid>44986</parentid>

      <timestamp>2012-10-31T08:56:35Z</timestamp>

      <contributor>

        <username>Hydriz</username>

        <id>320</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|tlwiki */ Aprika</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="6578" id="45090" />

      <sha1>0y39igxeiyxkif5xm0ekjsi1csc401v</sha1>

    </revision>

    <revision>

      <id>45001</id>

      <parentid>44994</parentid>

      <timestamp>2012-10-31T08:56:36Z</timestamp>

      <contributor>

        <username>Hydriz</username>

        <id>320</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|tnwiki */ Aferika</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="6605" id="45097" />

      <sha1>px5ffnsg2xrt0zdo62p18vpgncskzty</sha1>

    </revision>

    <revision>

      <id>4


      <timestamp>2014-10-12T01:20:03Z</timestamp>

      <contributor>

        <username>AmaryllisGardener</username>

        <id>87430</id>

      </contributor>

      <comment>/* wbeditentity-update:0| */ [[MediaWiki_talk:Gadget-labelLister.js|labelLister]] [brh] label (Afríká)</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="57849" id="163611626" />

      <sha1>93ws8q1excwzru66jp1o3125c3ddkby</sha1>

    </revision>

    <revision>

      <id>164000511</id>

      <parentid>163152821</parentid>

      <timestamp>2014-10-15T18:58:37Z</timestamp>

      <contributor>

        <username>Dexbot</username>

        <id>24059</id>

      </contributor>

      <comment>/* wbsetsitelink-set-both:2|dawiki */ Afrika, [[Q17559452]]</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="57869" id="164460388" />

      <sha1>3zqmr0e5dqhofylz38e594zhkjlhha6</sha1>

    </revision>

 

...

      <text bytes="995322" id="966817395" />

      <sha1>nvrqfscxnub3r1kinnlt3bssz30yrwg</sha1>

    </revision>

    <revision>

      <id>959125562</id>

      <parentid>959125433</parentid>

      <timestamp>2019-06-10T09:38:12Z</timestamp>

      <contributor>

        <username>813gan</username>

        <id>3030127</id>

      </contributor>

      <comment>/* wbsetqualifier-add:1| */ [[Property:P585]]: 1995</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="995772" id="966817522" />

      <sha1>rrs67kmc7p3wva7mj804en085gjyorp</sha1>

    </revision>

    <revision>

      <id>959125688</id>

      <parentid>959125562</parentid>

      <timestamp>2019-06-10T09:38:23Z</timestamp>

      <contributor>

        <username>813gan</username>

        <id>3030127</id>

      </contributor>

      <comment>/* wbsetreference-add:2| */ [[Property:P4010]]: 2,936,481,868,854 Geary–Khamis dollar</comment>

      <model>wikibase-item</m


      <timestamp>2019-07-24T07:26:56Z</timestamp>

      <contributor>

        <username>FallingGravity</username>

        <id>46577</id>

      </contributor>

      <comment>/* wbsetclaim-create:2||1 */ [[Property:P6839]]: UsefulNotes/Japan</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="1102350" id="992723289" />

      <sha1>30nygn6a04919gy3kiaq6e0ggyc5h9z</sha1>

    </revision>

    <revision>

      <id>988057954</id>

      <parentid>984711571</parentid>

      <timestamp>2019-07-28T18:43:12Z</timestamp>

      <contributor>

        <username>Bouzinac</username>

        <id>1768955</id>

      </contributor>

      <comment>/* wbsetclaim-update:2||1 */ [[Property:P1334]]: 24°16'59"N, 153°59'11"E</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="1102353" id="996089349" />

      <sha1>n8o9yj0onbmhlc5yxj89m94ksjm7rhp</sha1>

    </revision>

    <revision>

   

      <text bytes="4796" id="46034" />

      <sha1>oroo41nu380gdbutw1yrd1jmeybuq44</sha1>

    </revision>

    <revision>

      <id>45945</id>

      <parentid>45938</parentid>

      <timestamp>2012-10-31T08:58:58Z</timestamp>

      <contributor>

        <username>Hydriz</username>

        <id>320</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|mkwiki */ Јужна Америка</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="4842" id="46041" />

      <sha1>byf5redcihldhcq6ljma4bae9al72sf</sha1>

    </revision>

    <revision>

      <id>45952</id>

      <parentid>45945</parentid>

      <timestamp>2012-10-31T08:58:59Z</timestamp>

      <contributor>

        <username>Hydriz</username>

        <id>320</id>

      </contributor>

      <comment>/* wbsetsitelink-set:1|mlwiki */ തെക്കേ അമേരിക്ക</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="4906" id="4


      <parentid>66402223</parentid>

      <timestamp>2013-08-25T18:23:49Z</timestamp>

      <contributor>

        <username>Barcex</username>

        <id>28330</id>

      </contributor>

      <comment>/* wbsetaliases-add:1|es */ Sudamérica</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="20495" id="66890547" />

      <sha1>ovum7twr7r1zlx95l70t14tgsqth81j</sha1>

    </revision>

    <revision>

      <id>66801741</id>

      <parentid>66801734</parentid>

      <timestamp>2013-08-25T18:23:56Z</timestamp>

      <contributor>

        <username>Barcex</username>

        <id>28330</id>

      </contributor>

      <comment>/* wbsetaliases-add:1|es */ Suramérica</comment>

      <model>wikibase-item</model>

      <format>application/json</format>

      <text bytes="20518" id="66890554" />

      <sha1>sw01cs4357ksiez1gnnoznc4e8irpxu</sha1>

    </revision>

    <revision>

      <id>67740281</id>

      <parentid>6680174

KeyboardInterrupt: 

In [10]:
#parse the file, calculate lightdump information, output to outfile
def parse_metadata_to_lightdump(filepath, outfile, outdir, articles=[]):

    from lxml import etree
    import re

    context = etree.iterparse(filepath, tag='{http://www.mediawiki.org/xml/export-0.10/}page', encoding='utf-8')
    nsmap = {'ns': 'http://www.mediawiki.org/xml/export-0.10/'}

    article_count = len(articles) if len(articles) != 0 else -1
    
    revi_header = "^^^_"

    page_dicts = {}
            
    if not os.path.exists(outdir):
        os.makedirs(outdir, exist_ok=True)

    with open(outdir + "/" + outfile, 'w') as file:
        file.write("")

    for event, elem in context:

        page_title = '_'.join(elem.find('ns:title', nsmap).text.split())
        page_id = elem.find('ns:id', nsmap).text
        revisions = elem.findall('ns:revision', nsmap)

        rev_dicts = []
        
        if len(articles) != 0 and page_title not in articles:
            elem.clear()
            while elem.getprevious() is not None:
                del elem.getparent()[0]
            continue
        
#         print(page_title)
#         print(len(revisions))
        
        for revision in revisions:
            rev = {}
            
            rev['revision_id'] = revision.find("ns:id", nsmap).text
            rev['revision_parentid'] = revision.find("ns:parentid", nsmap).text if revision.find("ns:parentid", nsmap) != None else None
            rev['timestamp'] = revision.find("ns:timestamp", nsmap).text
            rev['sha1'] = revision.find("ns:sha1", nsmap).text
            rev['text_bytes'] = revision.find("ns:text", nsmap).attrib['bytes']
            
#             print(rev['text_bytes'])
             
            #getting contributer info
            contributor_info = revision.find("ns:contributor", nsmap)
            revision_contributor_username = contributor_info.find("ns:username", nsmap).text if contributor_info.find("ns:username", nsmap) != None else None
            revision_contributor_id = contributor_info.find("ns:id", nsmap).text if contributor_info.find("ns:id", nsmap) != None else None
            revision_contributor_ip = contributor_info.find("ns:ip", nsmap).text if contributor_info.find("ns:ip", nsmap) != None else None
            
            if revision_contributor_username != None:
                revision_contributor_username = "_".join(revision_contributor_username.split())
                rev['contributor'] = revision_contributor_username
            elif revision_contributor_ip != None:
                rev['contributor'] = revision_contributor_ip
            else:
                rev['contributor'] = "null"
                
            rev_dicts.append(rev)
            
        rev_dicts.sort(key=lambda x: x['timestamp'])

        version = 1
        page_results = []

        for i in range(len(rev_dicts)):

            temp_rev = MetadataRevision(rev_dicts[i]['timestamp'], 0, version, rev_dicts[i]['contributor'], \
                                rev_dicts[i]['revision_id'], rev_dicts[i]['revision_parentid'], \
                                rev_dicts[i]['sha1'], rev_dicts[i]['text_bytes'])
            if rev_dicts[i]['revision_parentid'] == None:
                page_results.append(temp_rev)
                version += 1    
            else:
                # find the point we revert to
                min_ind = len(page_results) - 1
                while min_ind > 0:
                    if page_results[min_ind].sha1 == rev_dicts[i]['sha1']:
                        temp_rev.version = page_results[min_ind].version
                        temp_rev.revert = 1
                        page_results.append(temp_rev)
                        break
                    min_ind -= 1

                if min_ind == 0:
                    page_results.append(temp_rev)
                    version += 1
        
        if len(articles) == 0 or page_title in articles:
            article_count -= 1
    
            print("Writing {} {} revisions to {}".format(page_title, len(page_results), outfile))
            with open(outdir + "/" + outfile, 'a') as file:
                with open(outdir + "/" + 'article_titles.txt', 'w') as article_file:
                    file.write(page_title.strip() + '\n')
                    article_file.write(page_title.strip() + "\n")
                    for i in range(len(page_results) - 1, -1, -1):
                        file.write(page_results[i].__str__() + "\n")
            
        # release uneeded XML from memory
        elem.clear()
        while elem.getprevious() is not None:
            del elem.getparent()[0]

        if article_count != -1 and article_count == 0:
            break

    del context

In [11]:
class MetadataRevision:
    def __init__(self, timestamp, revert, version, contributor, revision_id, revision_parentid, sha1, text_bytes):
        self.timestamp = timestamp
        self.revert = revert
        self.version = version
        self.contributor = contributor
        self.revision_id = revision_id
        self.revision_parentid = revision_parentid
        self.sha1 = sha1
        self.text_bytes = text_bytes
        
    def __repr__(self):
        return [self.timestamp, self.revert, self.version, self.contributor, self.revision_id, self.revision_parentid]
        
    def __str__(self):
        try:
            return "^^^_" + self.timestamp + " " + str(self.revert) + " " + str(self.version) + " " + str(self.text_bytes) + " " + self.contributor
        except:
            print(self.timestamp)
            print(self.revert)
            print(self.version)
            print(self.contributor)
    
    def get_revision_id(self):
        return self.revision_id

In [12]:

#parse enwiki to lightdump
file_to_parse = "../data/raw/extracted/metadata-20200101-1.xml"
lightdump_filename = "tempdump.txt"
temp_dir = "../data/temp"
articles = []

parse_metadata_to_lightdump(file_to_parse , lightdump_filename, temp_dir, articles)

Writing AccessibleComputing 13 revisions to tempdump.txt
Writing Anarchism 18885 revisions to tempdump.txt
Writing AfghanistanHistory 6 revisions to tempdump.txt
Writing AfghanistanGeography 7 revisions to tempdump.txt
Writing AfghanistanPeople 8 revisions to tempdump.txt
Writing AfghanistanCommunications 5 revisions to tempdump.txt
Writing AfghanistanTransportations 9 revisions to tempdump.txt
Writing AfghanistanMilitary 6 revisions to tempdump.txt
Writing AfghanistanTransnationalIssues 5 revisions to tempdump.txt
Writing AssistiveTechnology 6 revisions to tempdump.txt
Writing AmoeboidTaxa 8 revisions to tempdump.txt
Writing Autism 10276 revisions to tempdump.txt
Writing AlbaniaHistory 6 revisions to tempdump.txt
Writing AlbaniaPeople 5 revisions to tempdump.txt
Writing AsWeMayThink 6 revisions to tempdump.txt
Writing AlbaniaGovernment 5 revisions to tempdump.txt
Writing AlbaniaEconomy 6 revisions to tempdump.txt
Writing Albedo 1182 revisions to tempdump.txt
Writing AfroAsiaticLanguag

Writing Animal_(disambiguation) 473 revisions to tempdump.txt
Writing Aardvark 3198 revisions to tempdump.txt
Writing Aardwolf 649 revisions to tempdump.txt
Writing Adobe 1230 revisions to tempdump.txt
Writing Adventure 1065 revisions to tempdump.txt
Writing Amaltheia 3 revisions to tempdump.txt
Writing Analysis_of_Variance 5 revisions to tempdump.txt
Writing Asia 7818 revisions to tempdump.txt
Writing Aruba 3717 revisions to tempdump.txt
Writing Articles_of_Confederation 6239 revisions to tempdump.txt
Writing Talk:Archaeology 414 revisions to tempdump.txt
Writing Archaeology/Broch 6 revisions to tempdump.txt
Writing Asia_Minor_(disambiguation) 123 revisions to tempdump.txt
Writing Aa_River 165 revisions to tempdump.txt
Writing Atlantic_Ocean 5204 revisions to tempdump.txt
Writing Arthur_Schopenhauer 0 revisions to tempdump.txt
Writing Angola 5164 revisions to tempdump.txt
Writing Demographics_of_Angola 289 revisions to tempdump.txt
Writing Politics_of_Angola 188 revisions to tempdump.

Writing Angst 839 revisions to tempdump.txt
Writing Anxiety 4223 revisions to tempdump.txt
Writing A.A._Milne 3 revisions to tempdump.txt
Writing A._A._Milne 1562 revisions to tempdump.txt
Writing Asociación_Alumni 134 revisions to tempdump.txt
Writing Alumna 13 revisions to tempdump.txt
Writing Axiom 1285 revisions to tempdump.txt
Writing Alpha 552 revisions to tempdump.txt
Writing Alvin_Toffler 684 revisions to tempdump.txt
Writing The_Amazing_Spider-Man 0 revisions to tempdump.txt
Writing AM 636 revisions to tempdump.txt
Writing Talk:Axiom 148 revisions to tempdump.txt
Writing Automated_Alice/XII 3 revisions to tempdump.txt
Writing Automated_Alice/XI 3 revisions to tempdump.txt
Writing Automated_Alice/X 3 revisions to tempdump.txt
Writing Automated_Alice/IX 4 revisions to tempdump.txt
Writing Automated_Alice/VIII 3 revisions to tempdump.txt
Writing Automated_Alice/VI 3 revisions to tempdump.txt
Writing Automated_Alice/VII 3 revisions to tempdump.txt
Writing Automated_Alice/V 3 revis

Writing Abner_Doubleday 1089 revisions to tempdump.txt
Writing America's_National_Game 25 revisions to tempdump.txt
Writing Talk:Analysis 75 revisions to tempdump.txt
Writing Amplitude_modulation 994 revisions to tempdump.txt
Writing Augustin-Jean_Fresnel 513 revisions to tempdump.txt
Writing Abbot 528 revisions to tempdump.txt
Writing Ardipithecus 788 revisions to tempdump.txt
Writing Assembly_line 2180 revisions to tempdump.txt
Writing Adelaide 5596 revisions to tempdump.txt
Writing AK47 11 revisions to tempdump.txt
Writing Alan_Garner 493 revisions to tempdump.txt
Writing Amhrann_na_bhFiann 5 revisions to tempdump.txt
Writing August_2 0 revisions to tempdump.txt
Writing Atlantic_(disambiguation) 181 revisions to tempdump.txt
Writing Algebraic_number 525 revisions to tempdump.txt
Writing Automorphism 220 revisions to tempdump.txt
Writing Talk:Algebraic_number 96 revisions to tempdump.txt
Writing Accordion 2762 revisions to tempdump.txt
Writing Artificial_intelligence 0 revisions to t

Writing Apache_webserver 5 revisions to tempdump.txt
Writing Apatosaurus 2268 revisions to tempdump.txt
Writing Allosaurus 2394 revisions to tempdump.txt
Writing AK-47 11151 revisions to tempdump.txt
Writing Atanasoff–Berry_computer 705 revisions to tempdump.txt
Writing Andes 0 revisions to tempdump.txt
Writing Anderida 27 revisions to tempdump.txt
Writing Ancylopoda 68 revisions to tempdump.txt
Writing Anchor 1254 revisions to tempdump.txt
Writing Anbar_(town) 172 revisions to tempdump.txt
Writing Anazarbus 156 revisions to tempdump.txt
Writing Anagram 2057 revisions to tempdump.txt
Writing Anadyr_River 134 revisions to tempdump.txt
Writing André-Marie_Ampère 1646 revisions to tempdump.txt
Writing Ammonia 4017 revisions to tempdump.txt
Writing Amethyst 2142 revisions to tempdump.txt
Writing Albertosaurus 999 revisions to tempdump.txt
Writing Assembly_language 2515 revisions to tempdump.txt
Writing Ambrosia 779 revisions to tempdump.txt
Writing Ambrose 1354 revisions to tempdump.txt
Wr

...

Writing Mark_Whitacre 1001 revisions to tempdump.txt
Writing Saint_Methodius_of_Thessaloniki 244 revisions to tempdump.txt
Writing Marakesh_Agreement 7 revisions to tempdump.txt
Writing Talk:Marakesh_Agreement 2 revisions to tempdump.txt
Writing Marrakesh_Agreement 83 revisions to tempdump.txt
Writing Talk:Marrakesh_Agreement 7 revisions to tempdump.txt
Writing Mad 562 revisions to tempdump.txt
Writing Mammals 6 revisions to tempdump.txt
Writing Mainz 1201 revisions to tempdump.txt
Writing Mujahedin 4 revisions to tempdump.txt
Writing Talk:Masturbation 3451 revisions to tempdump.txt
Writing Maria_Feodorovna_(Dagmar_of_Denmark) 1329 revisions to tempdump.txt
Writing Montauban 257 revisions to tempdump.txt
Writing Rail_transport_modelling 1417 revisions to tempdump.txt
Writing Morphophonology 211 revisions to tempdump.txt
Writing Mirror 2798 revisions to tempdump.txt
Writing Mindanao 1781 revisions to tempdump.txt
Writing Moveable_feast 254 revisions to tempdump.txt
Writing Mark_McGwire 

Writing M'Naghten_rules 381 revisions to tempdump.txt
Writing Mongolism 33 revisions to tempdump.txt
Writing Mineraloid 200 revisions to tempdump.txt
Writing Mathematical_formulation_of_quantum_mechanics 637 revisions to tempdump.txt
Writing Talk:Marvin_Minsky 231 revisions to tempdump.txt
Writing Talk:Mechanized_force 9 revisions to tempdump.txt
Writing Multiple-document_interface 289 revisions to tempdump.txt
Writing MDI 150 revisions to tempdump.txt
Writing Microlith 230 revisions to tempdump.txt
Writing Menorah_(Temple) 1123 revisions to tempdump.txt
Writing Pointing_device_gesture 342 revisions to tempdump.txt
Writing Maglev_(disambiguation) 78 revisions to tempdump.txt
Writing Talk:Maglev_(disambiguation) 19 revisions to tempdump.txt
Writing Monorail 1601 revisions to tempdump.txt
Writing Michael_Halliday 344 revisions to tempdump.txt
Writing Muslim_Brotherhood 0 revisions to tempdump.txt
Writing Maglevs 3 revisions to tempdump.txt
Writing Moctezuma_I 769 revisions to tempdump.tx

Writing Matzo 1118 revisions to tempdump.txt
Writing User:Mark 256 revisions to tempdump.txt
Writing Michel_Tremblay 305 revisions to tempdump.txt
Writing Supervised_learning 403 revisions to tempdump.txt
Writing Martin_Helwig 63 revisions to tempdump.txt
Writing Map_maker 6 revisions to tempdump.txt
Writing Macro_virus 318 revisions to tempdump.txt
Writing Microsoft_Access 2548 revisions to tempdump.txt
Writing Talk:Map_makers 2 revisions to tempdump.txt
Writing Malthusian 7 revisions to tempdump.txt
Writing Talk:Metis 4 revisions to tempdump.txt
Writing Malthus 5 revisions to tempdump.txt
Writing Metabolic_pathway 424 revisions to tempdump.txt
Writing Malthusian_catastrophe 825 revisions to tempdump.txt
Writing Millennialism 630 revisions to tempdump.txt
Writing Talk:Minarchism 231 revisions to tempdump.txt
Writing Might_and_Magic 388 revisions to tempdump.txt
Writing Malopolska 3 revisions to tempdump.txt
Writing Adobe_Flash 5800 revisions to tempdump.txt
Writing Brainwashing 3421 r

Writing Natural_monopoly 691 revisions to tempdump.txt
Writing NonEmpty 6 revisions to tempdump.txt
Writing Natural_selection 0 revisions to tempdump.txt


KeyboardInterrupt: 